In [1]:
import yfinance as yf
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

In [2]:
# Get the data from tsm and spotifyth inteval of 30 minutes

tm = yf.Ticker("TM")
spotify = yf.Ticker("SPOT")

tm_data = tm.history(period="60d", interval="2m")
spotify_data = spotify.history(period="60d", interval="2m")

In [3]:
# plot both tickers on go figure

fig = go.Figure()
fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'], name='tm'))
fig.add_trace(go.Scatter(x=spotify_data.index, y=spotify_data['Close'], name='spotify'))

fig.show()

In [4]:
print(tm_data)

                                 Open        High         Low       Close  \
Datetime                                                                    
2024-03-15 09:30:00-04:00  234.910004  234.910004  234.910004  234.910004   
2024-03-15 09:32:00-04:00  234.970001  234.970001  234.510101  234.619995   
2024-03-15 09:34:00-04:00  234.500000  234.500107  234.500000  234.500107   
2024-03-15 09:40:00-04:00  234.585007  234.669998  234.585007  234.669998   
2024-03-15 09:42:00-04:00  234.820007  234.912003  234.779999  234.779999   
...                               ...         ...         ...         ...   
2024-04-26 15:50:00-04:00  226.850006  226.949997  226.850006  226.869995   
2024-04-26 15:52:00-04:00  226.880005  226.910004  226.781403  226.860001   
2024-04-26 15:54:00-04:00  226.669998  226.824997  226.669998  226.720001   
2024-04-26 15:56:00-04:00  226.720001  226.820007  226.699997  226.729996   
2024-04-26 15:58:00-04:00  226.720001  226.789993  226.660004  226.669998   

In [5]:
# plot eith candle stick

fig = go.Figure(data=[go.Candlestick(x=tm_data.index,
                open=tm_data['Open'],
                high=tm_data['High'],
                low=tm_data['Low'],
                close=tm_data['Close'])])

# plot moving average of 20 ticks and 80 ticks

fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'].rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'].rolling(window=20).mean(), name='20 Ticks MA'))

fig.show()

In [6]:
# count the number of times the 5 ticks MA crosses the 20 ticks MA

tm_data['5T_MA'] = tm_data['Close'].rolling(window=5).mean()
tm_data['20T_MA'] = tm_data['Close'].rolling(window=20).mean()

tm_data['signal'] = np.where(tm_data['5T_MA'] > tm_data['20T_MA'], 1, 0)
tm_data['signal'] = tm_data['signal'].diff()

print(tm_data['signal'].value_counts())

# plot the buy and sell signals

fig = go.Figure(data=[go.Candlestick(x=tm_data.index,
                open=tm_data['Open'],
                high=tm_data['High'],
                low=tm_data['Low'],
                close=tm_data['Close'])])

fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'].rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'].rolling(window=20).mean(), name='20 Ticks MA'))

buy_signals = tm_data[tm_data['signal'] == 1]
sell_signals = tm_data[tm_data['signal'] == -1]

fig.add_trace(go.Scatter(x=buy_signals.index, y=buy_signals['Close'], mode='markers', marker=dict(color='green', size=10), name='Buy Signal'))

fig.add_trace(go.Scatter(x=sell_signals.index, y=sell_signals['Close'], mode='markers', marker=dict(color='red', size=10), name='Sell Signal'))

fig.show()

signal
 0.0    4292
 1.0     149
-1.0     148
Name: count, dtype: int64


In [7]:
# calculate profit and loss

tm_data['buy_price'] = np.where(tm_data['signal'] == 1, tm_data['Close'], np.nan)
tm_data['sell_price'] = np.where(tm_data['signal'] == -1, tm_data['Close'], np.nan)

tm_data['buy_price'] = tm_data['buy_price'].ffill()
tm_data['sell_price'] = tm_data['sell_price'].ffill()

tm_data['PnL'] = tm_data['sell_price'] - tm_data['buy_price']

print(tm_data['PnL'].sum())

# plot the profit and loss

fig = go.Figure(data=[go.Candlestick(x=tm_data.index,
                open=tm_data['Open'],
                high=tm_data['High'],
                low=tm_data['Low'],
                close=tm_data['Close'])])

fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'].rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'].rolling(window=20).mean(), name='20 Ticks MA'))

buy_signals = tm_data[tm_data['signal'] == 1]
sell_signals = tm_data[tm_data['signal'] == -1]

fig.add_trace(go.Scatter(x=buy_signals.index, y=buy_signals['Close'], mode='markers', marker=dict(color='green', size=10), name='Buy Signal'))
fig.add_trace(go.Scatter(x=sell_signals.index, y=sell_signals['Close'], mode='markers', marker=dict(color='red', size=10), name='Sell Signal'))

fig.show()

-305.5574493408203


In [8]:
ratio_0 = (tm_data['Close'].iloc[0]) / (spotify_data['Close'].iloc[0])
ratio_0

0.9172588756876435

In [9]:
spotify_data['Close_NORM'] = spotify_data['Close'].multiply(ratio_0).round(6)

In [10]:
tm_spotify_dif = tm_data['Close'] - spotify_data['Close_NORM']
tm_spotify_dif

Datetime
2024-03-15 09:30:00-04:00   -3.378906e-07
2024-03-15 09:32:00-04:00    5.855412e-02
2024-03-15 09:34:00-04:00    1.817388e-01
2024-03-15 09:36:00-04:00             NaN
2024-03-15 09:38:00-04:00             NaN
                                 ...     
2024-04-26 15:50:00-04:00   -3.785092e+01
2024-04-26 15:52:00-04:00   -3.826451e+01
2024-04-26 15:54:00-04:00   -3.853291e+01
2024-04-26 15:56:00-04:00   -3.841744e+01
2024-04-26 15:58:00-04:00   -3.902321e+01
Length: 5845, dtype: float64

In [11]:
# Plot the difference between the two tickers

fig = go.Figure()
fig.add_trace(go.Scatter(x=tm_spotify_dif.index, y=tm_spotify_dif, name='tm - spotify'))

fig.show()

In [12]:
# Plot the two normalized tickers

fig = go.Figure()
fig.add_trace(go.Scatter(x=tm_data.index, y=tm_data['Close'], name='tm'))
fig.add_trace(go.Scatter(x=spotify_data.index, y=spotify_data['Close_NORM'], name = 'spotify'))

fig.show()

In [13]:
# Plot the difference and its moving average

fig = go.Figure()
fig.add_trace(go.Scatter(x=tm_spotify_dif.index, y=tm_spotify_dif, name='tmspotify'))
fig.add_trace(go.Scatter(x=tm_spotify_dif.index, y=tm_spotify_dif.rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=tm_spotify_dif.index, y=tm_spotify_dif.rolling(window=20).mean(), name='20 Ticks MA'))

fig.show()


In [14]:
tm_spotify_dif = tm_spotify_dif.to_frame()
tm_spotify_dif.columns = ['Close']
tm_spotify_dif

Close
Datetime                               
2024-03-15 09:30:00-04:00 -3.378906e-07
2024-03-15 09:32:00-04:00  5.855412e-02
2024-03-15 09:34:00-04:00  1.817388e-01
2024-03-15 09:36:00-04:00           NaN
2024-03-15 09:38:00-04:00           NaN
...                                 ...
2024-04-26 15:50:00-04:00 -3.785092e+01
2024-04-26 15:52:00-04:00 -3.826451e+01
2024-04-26 15:54:00-04:00 -3.853291e+01
2024-04-26 15:56:00-04:00 -3.841744e+01
2024-04-26 15:58:00-04:00 -3.902321e+01

[5845 rows x 1 columns]

In [15]:
tm_spotify_dif['10T_MA'] = tm_spotify_dif['Close'].rolling(window=10).mean()
tm_spotify_dif['60T_MA'] = tm_spotify_dif['Close'].rolling(window=60).mean()

tm_spotify_dif['signal'] = np.where(tm_spotify_dif['10T_MA'] > tm_spotify_dif['60T_MA'], 1, 0)
tm_spotify_dif['signal'] = tm_spotify_dif['signal'].diff()

print(tm_spotify_dif['signal'].value_counts())

# Plot the signals

fig = go.Figure()
fig.add_trace(go.Scatter(x=tm_spotify_dif.index, y=tm_spotify_dif['Close'], name='tmspotify'))
fig.add_trace(go.Scatter(x=tm_spotify_dif.index, y=tm_spotify_dif.rolling(window=10).mean()['Close'], name='10 Ticks MA'))
fig.add_trace(go.Scatter(x=tm_spotify_dif.index, y=tm_spotify_dif.rolling(window=60).mean()['Close'], name='60 Ticks MA'))

buy_signals = tm_spotify_dif[tm_spotify_dif['signal'] == 1]
sell_signals = tm_spotify_dif[tm_spotify_dif['signal'] == -1]

fig.add_trace(go.Scatter(x=buy_signals.index, y=buy_signals['Close'], mode='markers', marker=dict(color='green', size=10), name='Buy Signal'))
fig.add_trace(go.Scatter(x=sell_signals.index, y=sell_signals['Close'], mode='markers', marker=dict(color='red', size=10), name='Sell Signal'))

fig.show()


signal
0.0    5844
Name: count, dtype: int64


In [16]:
#Consider tmas the first and spotify as the second ticker.
#When there is a buy signal for tm, we buy tm and sell spotify.
#When there is a sell signal for tm we sell tm and buy spotify

In [17]:
#Copy signal column from difference dataframe to tm_dataframe
tm_data['signal'] = tm_spotify_dif['signal']
spotify_data['signal'] = -tm_spotify_dif['signal']